
# Single anatomical volume with 2D EPI with SNAKE-fMRI

This examples walks through the elementary components of SNAKE.

Here we proceed step by step and use the Python interface. A more integrated
alternative is to use the CLI ``snake-main``


In [ ]:
# Imports
import numpy as np
from snake.core.simulation import SimConfig, default_hardware, GreConfig
from snake.core.phantom import Phantom
from snake.core.smaps import get_smaps
from snake.core.sampling import EPI3dAcquisitionSampler

Setting up the base simulation Config.  This configuration holds all key
parameters for the simulation, describing the scanner parameters.



In [ ]:
sim_conf = SimConfig(
    max_sim_time=6,
    seq=GreConfig(TR=25, TE=30, FA=3),
    hardware=default_hardware,
    fov_mm=(181, 217, 181),
    shape=(60, 71, 60),
)
sim_conf.hardware.n_coils = 8

sim_conf

## Creating the base Phantom

The simulation acquires
the data describe in a phantom. A phantom consists of fuzzy segmentation of
head tissue, and their MR intrinsic parameters
(density, T1, T2, T2*,  magnetic susceptibilities)

Here we use Brainweb reference mask and values for convenience.



In [ ]:
phantom = Phantom.from_brainweb(sub_id=4, sim_conf=sim_conf)

# Here are the tissue availables and their parameters
phantom

## Setting up Acquisition Pattern and Initializing Result file.



In [ ]:
# The next piece of simulation is the acquisition trajectory.
# Here nothing fancy, we are using a EPI (fully sampled), that samples a 3D
# k-space (this akin to the 3D EPI sequence of XXXX)

sampler = EPI3dAcquisitionSampler(accelz=1, acsz=0.1, orderz="top-down")

smaps = None
if sim_conf.hardware.n_coils > 1:
    smaps = get_smaps(sim_conf.shape, n_coils=sim_conf.hardware.n_coils)

## Acquisition with Cartesian Engine

The generated file ``example_EPI.mrd`` does not contains any k-space data for
now, only the sampling trajectory. let's put some in. In order to do so, we
need to setup the **acquisition engine** that models the MR physics, and get
sampled at the specified k-space trajectory.

Here, we have a single frame to acquire with 60 slice (one EPI per slice), so
a single worker will be enough.



In [ ]:
from snake.core.engine import EPIAcquisitionEngine

engine = EPIAcquisitionEngine(model="T2s", slice_2d=True)  # use the 2D epi.

engine(
    "example_EPI2D.mrd",
    sampler=sampler,
    phantom=phantom,
    sim_conf=sim_conf,
    smaps=smaps,
    # worker_chunk_size=20,
    n_workers=1,
)

## Simple reconstruction

Getting k-space data is nice, but
SNAKE also provides rudimentary reconstruction tools to get images (and check
that we didn't mess up the acquisition process).
This is available in the companion package ``snake.toolkit``.

Loading the ``.mrd`` file to retrieve all information can be done using the
``ismrmd`` python package, but SNAKE provides convenient dataloaders, which are
more efficient, and take cares of managing underlying files access. As we are
showcasing the API, we will do things manually here, and use only core SNAKE.



In [ ]:
from snake.mrd_utils import CartesianFrameDataLoader

with CartesianFrameDataLoader("example_EPI2D.mrd") as data_loader:
    mask, kspace_data = data_loader.get_kspace_frame(0)

Reconstructing a Single Frame of fully sampled EPI boils down to performing a 3D IFFT:



In [ ]:
from scipy.fft import ifftn, ifftshift, fftshift

axes = (
    -2,
    -1,
)
image_data = ifftshift(
    ifftn(fftshift(kspace_data, axes=axes), axes=axes, norm="ortho"), axes=axes
)

# Take the square root sum of squares to get the magnitude image (SSOS)
image_data = np.sqrt(np.sum(np.abs(image_data) ** 2, axis=0))

In [ ]:
image_data

In [ ]:
import matplotlib.pyplot as plt
from snake.toolkit.plotting import axis3dcut

fig, ax = plt.subplots()

axis3dcut(image_data.squeeze().T, None, None, cbar=False, cuts=(40, 60, 40), ax=ax)
plt.show()